# Title
### explanation

In [26]:
import pandas as pd
import numpy as np  
from datetime import datetime
import psycopg2 
import altair as alt

from functions import Team_Augury_SQL_func
from functions import Team_Augury_feature_functions

In [15]:
conn = psycopg2.connect(
    host = 'capstone697.czsaza7am68b.us-east-1.rds.amazonaws.com' ,
    port = '5432',
    database = 'Capstone697', 
    user = 'read_o',  
    password = 'EAC697Reddit' , 
    connect_timeout=3)

### cur = conn.cursor()

### NEW SQL Variables
sr_id = '(4, 31760, 31764, 31766)'   #[(4, '2qhhq', 'investing'), (16, 'mouw', 'science'), (130, '2qh1i', 'AskReddit'), (18162, '2qh3l', 'news'), (31760, '2qjuv', 'StockMarket'), (31764, '2qjfk', 'stocks'), (31766, '2th52', 'wallstreetbets')]
#sr_id = '(4, 31760, 31764, 31766, 16, 130, 18162)' 
lower_timestamp = '2022-03-01 14:30:00'  
upper_timestamp = '2022-03-28 08:00:00'#'2022-04-04 08:00:00'#'2022-03-28 08:00:00'  #batch 260 3/1/2022 14:37:31  #'2022-03-28 08:00:00'  #batch 900	2022-03-28 07:21:27


In [16]:
### pull data from our database
post_data, comments_data = Team_Augury_SQL_func.sql_by_timestamp(conn,sr_id,lower_timestamp,upper_timestamp)
# print('-- raw posts --')
# display(post_data)
# print('-- raw comments --' )
# display(comments_data)

C:\Users\erikl\anaconda3\envs\Capstone697\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\erikl\anaconda3\envs\Capstone697\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\erikl\anaconda3\envs\Capstone697\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\erikl\anaconda3\envs\Capstone697\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQL

### Initial data checks of our EDA sample

In [17]:
df = post_data.copy()
print('unique post_id:', len(df.post_id.unique()))
print('unique post_id hr==0:', len(df.post_id[df.hours_since_created==0].unique()))
print('unique post_id hr==3:', len(df.post_id[df.hours_since_created==3].unique()))

unique post_id: 1219
unique post_id hr==0: 1171
unique post_id hr==3: 1133


In [18]:
df[df.hours_since_created==0][['sr','post_id']].drop_duplicates().groupby('sr').count()

post_id
sr            
4          291
31760      217
31764      308
31766      355

In [19]:
### add a column for upvotes / hours, our proxy for how "popularity" or "hot" posts are ranked on Reddit
post_data = post_data.copy()
post_data = post_data[post_data.hours_since_created<25]
post_data['upvotes_vs_hours'] = post_data.apply(lambda x: x.post_upvotes/1 if x.hours_since_created==0 else x.post_upvotes/x.hours_since_created, axis=1)

#del comments_data

# EDA for our y-Variable: classifying "popular"

In [7]:
### Sphegetti chart of our sample set's "popularity" proxy
title='Post Popularity Proxy: upvotes / hours over 24 hours'

alt.data_transformers.enable('default', max_rows=None)

chart1 = alt.Chart(post_data[['post_id','hours_since_created','upvotes_vs_hours']]).mark_line(opacity=0.1,color='blue').encode(
    x=alt.X('hours_since_created:O'),
    y=alt.Y('upvotes_vs_hours:Q', scale=alt.Scale(domain=[0,120],clamp=True)),
    detail='post_id'
).properties(
    width = 750,
    height = 500,
    title = '  {}'.format(title)
)
chart1

alt.Chart(...)

In [7]:
# title='[zoomed in] upvotes_vs_hours over 24 hours'

# alt.data_transformers.enable('default', max_rows=None)

# chart = alt.Chart(post_data[post_data.hours_since_created<=6]).mark_line(opacity=0.1,color='red').encode(
#     x=alt.X('hours_since_created:O', ),
#     y=alt.Y('upvotes_vs_hours', scale=alt.Scale(domain=[0,300],clamp=True)),
#     detail='post_id'
# ).properties(
#     width = 750,
#     height = 500,
#     title = '  {}'.format(title)
# )
# chart

## Narrowing down our target "popularity" threshold by examining percentiles of the data

In [11]:
chart_df = post_data.copy().groupby(['hours_since_created'])['upvotes_vs_hours'].describe(percentiles=[0.5,.8, .90])
#df = df.rename({'50%':'median'},axis=1)
chart_df = chart_df[['50%','80%','90%']]
chart_df = chart_df.rename({'50%':'Top Half (50%)','80%':'Top Quintile (80%)','90%':'Top Decile (90%)'}, axis=1)
chart_df = chart_df.stack(level=- 1, dropna=False).reset_index()
chart_df = chart_df.rename({'level_1':'percentile_of_posts', 0:'upvotes_vs_hours'}, axis=1)
chart_df

hours_since_created percentile_of_posts  upvotes_vs_hours
0                     0      Top Half (50%)          2.000000
1                     0  Top Quintile (80%)          6.000000
2                     0    Top Decile (90%)         11.000000
3                     1      Top Half (50%)          3.000000
4                     1  Top Quintile (80%)         18.000000
..                  ...                 ...               ...
70                   23  Top Quintile (80%)          6.182609
71                   23    Top Decile (90%)         25.273913
72                   24      Top Half (50%)          0.416667
73                   24  Top Quintile (80%)          6.200000
74                   24    Top Decile (90%)         24.520833

[75 rows x 3 columns]

In [12]:
title = "Percentile Thresholds of our Popularity Proxy: upvotes_vs_hours over 24 hours"

chart2 = alt.Chart(chart_df).mark_line().encode(
    x=alt.X('hours_since_created:O'),
    y=alt.Y('upvotes_vs_hours:Q', scale=alt.Scale(domain=[0,120],clamp=True)),
    color = alt.Color('percentile_of_posts',legend = alt.Legend( orient="top-right", title=None), scale = alt.Scale(range=['orange','yellow','red'])),
    
).properties(
    width = 750,
    height = 500,
    title = '  {}'.format(title)
)
chart2

alt.Chart(...)

### Layer the two charts together for our Blog


In [13]:
chart1 + chart2

alt.LayerChart(...)

In [14]:
### look at the data
post_data.copy()[post_data.hours_since_created==3].describe([0.5,.8,.9])

batch_id       post_id  hours_since_created            sr  \
count  1133.000000   1133.000000               1133.0   1133.000000   
mean    672.357458  45620.358341                  3.0  23410.377758   
std     147.540556  12062.375247                  0.0  13989.134644   
min     263.000000  14554.000000                  3.0      4.000000   
50%     682.000000  46276.000000                  3.0  31764.000000   
80%     814.000000  57462.600000                  3.0  31766.000000   
90%     855.800000  61107.800000                  3.0  31766.000000   
max     900.000000  64793.000000                  3.0  31766.000000   

       post_upvotes  number_comments  post_author_karma  upvotes_vs_hours  
count   1133.000000      1133.000000        1133.000000       1133.000000  
mean      76.799647        29.050309       11327.788173         25.599882  
std      356.233910        72.907549       44248.315441        118.744637  
min        0.000000         0.000000        -100.000000          0.000000  
50%        5.000000        11.000000        1681.000000          1.666667  
80%       39.600000        35.600000       11066.200000         13.200000  
90%      129.600000        61.000000       25722.200000         43.200000  
max     6064.000000      1210.000000      969007.000000       2021.333333

# Basic correlation analyses

Looking at Correlation number of comments and upvotes, as at 8:19 AM 7 Apr still WIP

In [12]:
# df.head()

batch_id       time_of_batch  post_id  hours_since_created  sr  \
0       260 2022-03-01 14:37:31     9388                   15   4   
1       260 2022-03-01 14:37:31    14554                    0   4   
2       260 2022-03-01 14:37:31     7560                   20   4   
3       260 2022-03-01 14:37:31    13236                    4   4   
4       260 2022-03-01 14:37:31     6544                   23   4   

                                           post_text  post_upvotes  \
0                    How would the RSX get Delisted?            15   
1                   Investment options for children?             1   
2  My bank has screwed me over multiple times, lo...             0   
3  Ukraine supplies 70% of the world's neon. Chip...           692   
4  Does it make sense to invest in Ukrainian bond...             0   

   number_comments     post_created_at  post_author_karma  
0               12 2022-02-28 23:21:42               6625  
1                5 2022-03-01 14:18:19              30364  
2               26 2022-02-28 18:15:25               7689  
3               73 2022-03-01 10:13:53             265073  
4               11 2022-02-28 15:24:40                149

In [16]:
# cor_data_simple = df[['post_upvotes','number_comments']].corr()
# cor_data_simple.head()

post_upvotes  number_comments
post_upvotes         1.000000         0.734256
number_comments      0.734256         1.000000

In [27]:
# cor_data = df[['post_upvotes','number_comments','time_of_batch','hours_since_created','post_author_karma']].corr().stack().reset_index().rename(columns={0: 'correlation', 'level_0': 'variable', 'level_1': 'variable2'})
# cor_data['correlation_label'] = cor_data['correlation'].map('{:.2f}'.format)
# cor_data.head()

variable            variable2  correlation correlation_label
0     post_upvotes         post_upvotes     1.000000              1.00
1     post_upvotes      number_comments     0.734256              0.73
2     post_upvotes  hours_since_created     0.078384              0.08
3     post_upvotes    post_author_karma     0.070361              0.07
4  number_comments         post_upvotes     0.734256              0.73

In [29]:
# base = alt.Chart(cor_data).encode(
#     x='variable2:O',
#     y='variable:O'    
# )

# # Text layer with correlation labels
# # Colors are for easier readability
# text = base.mark_text().encode(
#     text='correlation_label',
#     color=alt.condition(
#         alt.datum.correlation > 0.5, 
#         alt.value('white'),
#         alt.value('black')
#     )
# )

# # The correlation heatmap itself
# cor_plot = base.mark_rect().encode(
#     color='correlation:Q'
# ).properties(height=200, width = 200)

# cor_plot + text # The '+' means overlaying the text and rect layer

alt.LayerChart(...)

# Correlations of "popularity" vs temporal data (day of week and hour of day)
### Can we see variation in when posts are created and their popularity ?

In [70]:
### Basic feature addtions for post-only data
feature_df = Team_Augury_feature_functions.post_basic_features(post_data.copy())
### Basic feature additions for comments (avg's)
feature_df = feature_df.merge( Team_Augury_feature_functions.comment_basic_features(comments_data.copy()) , how='left',on=['batch_id','post_id'])
print(feature_df.columns)


Index(['batch_id', 'time_of_batch', 'post_id', 'hours_since_created', 'sr',
       'post_text', 'post_upvotes', 'number_comments', 'post_created_at',
       'post_author_karma', 'upvotes_vs_hours', 'number_comments_vs_hrs',
       'time_hour', 'day_of_week', 'avg_comment_upvotes_vs_hrs',
       'avg_comment_author_karma', 'avg_comment_time_hour',
       'avg_comment_day_of_week'],
      dtype='object')


In [71]:
#feature_df

batch_id       time_of_batch  post_id  hours_since_created     sr  \
0           260 2022-03-01 14:37:31     9388                   15      4   
1           260 2022-03-01 14:37:31    14554                    0      4   
2           260 2022-03-01 14:37:31     7560                   20      4   
3           260 2022-03-01 14:37:31    13236                    4      4   
4           260 2022-03-01 14:37:31     6544                   23      4   
...         ...                 ...      ...                  ...    ...   
27203       900 2022-03-28 07:21:27    64386                    8  31764   
27204       900 2022-03-28 07:21:27    64877                    2  31766   
27205       900 2022-03-28 07:21:27    63847                   14  31764   
27206       900 2022-03-28 07:21:27    64137                   11  31764   
27207       900 2022-03-28 07:21:27    63994                   13  31764   

                                               post_text  post_upvotes  \
0                        How would the RSX get Delisted?            15   
1                       Investment options for children?             1   
2      My bank has screwed me over multiple times, lo...             0   
3      Ukraine supplies 70% of the world's neon. Chip...           692   
4      Does it make sense to invest in Ukrainian bond...             0   
...                                                  ...           ...   
27203  How do you guys feel about the upcoming Reddit...           151   
27204     Using Robinhood's instant deposit as leverage?             0   
27205                           Elon Musk’s Social Media             0   
27206            Cheapest way to buy US Stocks with GBP?             0   
27207  Investors who started in their 30's - Where ar...           259   

       number_comments     post_created_at  post_author_karma  \
0                   12 2022-02-28 23:21:42               6625   
1                    5 2022-03-01 14:18:19              30364   
2                   26 2022-02-28 18:15:25               7689   
3                   73 2022-03-01 10:13:53             265073   
4                   11 2022-02-28 15:24:40                149   
...                ...                 ...                ...   
27203              187 2022-03-27 23:12:16                529   
27204               13 2022-03-28 04:51:47                 38   
27205               21 2022-03-27 17:14:02               2108   
27206               14 2022-03-27 19:41:11                359   
27207              179 2022-03-27 18:13:24              26655   

       upvotes_vs_hours  number_comments_vs_hrs  time_hour  day_of_week  \
0              1.000000                0.800000         23            0   
1              1.000000                5.000000         14            1   
2              0.000000                1.300000         18            0   
3            173.000000               18.250000         10            1   
4              0.000000                0.478261         15            0   
...                 ...                     ...        ...          ...   
27203         18.875000               23.375000         23            6   
27204          0.000000                6.500000          4            0   
27205          0.000000                1.500000         17            6   
27206          0.000000                1.272727         19            6   
27207         19.923077               13.769231         18            6   

       avg_comment_upvotes_vs_hrs  avg_comment_author_karma  \
0                        0.200000                   14071.0   
1                        1.200000                   23723.6   
2                        0.920000                   66538.8   
3                       19.750000                   51834.8   
4                        0.182609                    2582.8   
...                           ...                       ...   
27203                   12.800000                   13945.0   
27204              

In [126]:
### days of the week vs popularity
df = feature_df.copy()
### what is average popularity for each post through its lifecycle?
df = df[['post_id','day_of_week','upvotes_vs_hours']].groupby(['post_id','day_of_week']).mean().reset_index()#.pivot(index='post_id',columns='day_of_week',values='upvotes_vs_hours')#.mean()#.fillna(0.0)#.corr(method='spearman').round(2)
df = df.pivot(index='post_id',columns='day_of_week',values='upvotes_vs_hours')
df = df.stack().reset_index().rename({0:'avg_popularity_over_life'}, axis=1)
### what is the average max popularity by day of the week?
df.groupby('day_of_week')['avg_popularity_over_life'].mean()

day_of_week
0     8.831729
1    25.526799
2     8.665443
3    27.233581
4    38.516206
5    20.549736
6    23.573509
Name: avg_popularity_over_life, dtype: float64

In [128]:
### Check of day_of_week index

def day_num_func(ts): 
    return ts.day_of_week

def day_func(ts):   
    return ts.day_name()

print('weekday:',day_func(pd.to_datetime('2022-03-01'))) 
print('index:',day_num_func(pd.to_datetime('2022-03-01'))) 

weekday: Tuesday
index: 1


In [129]:
### hours of the day vs popularity
df = feature_df.copy()
### what is average popularity for each post through its lifecycle?
df = df[['post_id','time_hour','upvotes_vs_hours']].groupby(['post_id','time_hour']).mean().reset_index()#.pivot(index='post_id',columns='day_of_week',values='upvotes_vs_hours')#.mean()#.fillna(0.0)#.corr(method='spearman').round(2)
df = df.pivot(index='post_id',columns='time_hour',values='upvotes_vs_hours')
df = df.stack().reset_index().rename({0:'avg_popularity_over_life'}, axis=1)
### what is the average max popularity by day of the week?
df.groupby('time_hour')['avg_popularity_over_life'].mean()

time_hour
0      8.812411
1     21.480299
2     10.036281
3     11.415132
4     17.802940
5     21.388972
6     12.360000
7     20.689132
8     10.935296
9     32.748851
10    18.869423
11    55.419464
12    17.105298
13    70.378282
14    14.621082
15    14.486070
16     3.720982
17    42.316619
18    21.078898
19    10.379498
20    13.147353
21    22.875116
22    29.601755
23    22.929798
Name: avg_popularity_over_life, dtype: float64

# Correlations of some basic data about posts and comments versus popularity

In [130]:
### Basic feature addtions for post-only data
feature_df = Team_Augury_feature_functions.post_basic_features(post_data.copy())
### Basic feature additions for comments (avg's)
feature_df = feature_df.merge( Team_Augury_feature_functions.comment_basic_features(comments_data.copy()) , how='left',on=['batch_id','post_id'])
print(feature_df.columns)


Index(['batch_id', 'time_of_batch', 'post_id', 'hours_since_created', 'sr',
       'post_text', 'post_upvotes', 'number_comments', 'post_created_at',
       'post_author_karma', 'upvotes_vs_hours', 'number_comments_vs_hrs',
       'time_hour', 'day_of_week', 'avg_comment_upvotes_vs_hrs',
       'avg_comment_author_karma', 'avg_comment_time_hour',
       'avg_comment_day_of_week'],
      dtype='object')


In [131]:
### correlation table of some basic post and comment data
df = feature_df.copy()
df[['upvotes_vs_hours', 'post_author_karma', 'number_comments_vs_hrs',
       'avg_comment_upvotes_vs_hrs', 'avg_comment_author_karma', 
   ]].corr().round(2)

upvotes_vs_hours  post_author_karma  \
upvotes_vs_hours                        1.00               0.07   
post_author_karma                       0.07               1.00   
number_comments_vs_hrs                  0.68               0.06   
avg_comment_upvotes_vs_hrs              0.70               0.05   
avg_comment_author_karma                0.04               0.17   

                            number_comments_vs_hrs  \
upvotes_vs_hours                              0.68   
post_author_karma                             0.06   
number_comments_vs_hrs                        1.00   
avg_comment_upvotes_vs_hrs                    0.87   
avg_comment_author_karma                      0.01   

                            avg_comment_upvotes_vs_hrs  \
upvotes_vs_hours                                  0.70   
post_author_karma                                 0.05   
number_comments_vs_hrs                            0.87   
avg_comment_upvotes_vs_hrs                        1.00   
avg_comment_author_karma                          0.01   

                            avg_comment_author_karma  
upvotes_vs_hours                                0.04  
post_author_karma                               0.17  
number_comments_vs_hrs                          0.01  
avg_comment_upvotes_vs_hrs                      0.01  
avg_comment_author_karma                        1.00

In [132]:
### same as above but with altair chart
df = feature_df.copy()
df = df[['upvotes_vs_hours', 'post_author_karma', 'number_comments_vs_hrs',
       'avg_comment_upvotes_vs_hrs', 'avg_comment_author_karma', 
   ]].corr().round(2)
df = df.stack().reset_index().rename({'level_0':'item_1','level_1':'item_2'}, axis=1)
#alt.Chart(df).mark_rect().encode...
df

item_1                      item_2     0
0             upvotes_vs_hours            upvotes_vs_hours  1.00
1             upvotes_vs_hours           post_author_karma  0.07
2             upvotes_vs_hours      number_comments_vs_hrs  0.68
3             upvotes_vs_hours  avg_comment_upvotes_vs_hrs  0.70
4             upvotes_vs_hours    avg_comment_author_karma  0.04
5            post_author_karma            upvotes_vs_hours  0.07
6            post_author_karma           post_author_karma  1.00
7            post_author_karma      number_comments_vs_hrs  0.06
8            post_author_karma  avg_comment_upvotes_vs_hrs  0.05
9            post_author_karma    avg_comment_author_karma  0.17
10      number_comments_vs_hrs            upvotes_vs_hours  0.68
11      number_comments_vs_hrs           post_author_karma  0.06
12      number_comments_vs_hrs      number_comments_vs_hrs  1.00
13      number_comments_vs_hrs  avg_comment_upvotes_vs_hrs  0.87
14      number_comments_vs_hrs    avg_comment_author_karma  0.01
15  avg_comment_upvotes_vs_hrs            upvotes_vs_hours  0.70
16  avg_comment_upvotes_vs_hrs           post_author_karma  0.05
17  avg_comment_upvotes_vs_hrs      number_comments_vs_hrs  0.87
18  avg_comment_upvotes_vs_hrs  avg_comment_upvotes_vs_hrs  1.00
19  avg_comment_upvotes_vs_hrs    avg_comment_author_karma  0.01
20    avg_comment_author_karma            upvotes_vs_hours  0.04
21    avg_comment_author_karma           post_author_karma  0.17
22    avg_comment_author_karma      number_comments_vs_hrs  0.01
23    avg_comment_author_karma  avg_comment_upvotes_vs_hrs  0.01
24    avg_comment_author_karma    avg_comment_author_karma  1.00